In [1]:
# Importing Required Python Packages
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.set_option('display.max_columns',None)

In [2]:
# Loading Reduced feature Training set
X_train_red = pd.read_csv('X_train_final.csv')
y_train = pd.read_csv('y_train.final.csv')

In [3]:
# Loading Reduced feature Test set
X_test_red = pd.read_csv('X_test_final.csv')
y_test = pd.read_csv('y_test.final.csv')

## Model_9:  Keras Variable Layer Dense Model With SELU Activation & Tuned LR Rate

In [4]:
# Importing Optuna , Tensorflow & Keras
import optuna , tensorflow as tf

In [5]:
# Importing Keras
from tensorflow import keras

In [6]:
# Importing train test split from Sklearn to produce validation set
from sklearn.model_selection import train_test_split

In [7]:
# Importing the Sklearn's roc_auc_score module
from sklearn.metrics import roc_auc_score

In [8]:
# Performing train validation split with test size = .1 to provide more Training data to Neural Net
X_train_red_1, X_val, y_train_1, y_val = train_test_split(X_train_red, y_train, test_size=0.1, random_state=42,
                                                          stratify=y_train)

In [9]:
# defining class weight dictionary list for the imbalanced class
cl_weight = [{0:1.0,1:7.8761},{0:1.0,1:9.0},{0:1.0,1:10.0},{0:1.0,1:11.0},{0:1.0,1:12.0}]

In [10]:
# Importing os module
#import os

In [11]:
# Declaring the path for my logs directory in the current directory
#root_logdir =os.path.join(os.curdir,'my_logs')

In [10]:
# Declaring the path for the log run files
'''def get_run_logdir():
    import time
    run_id = time.strftime('run_%Y_%m_%d-%H_5M_%S')
    return os.path.join(root_logdir,run_id)'''

In [10]:
# Defining best roc_auc score
best_roc_auc = 0

In [11]:
# defining the objective function
def objective_wrappper_keras(X_tr, y_tr, X_val, y_val, cl_weight):
    '''
    Optimizes Keras neural net best parameters on the given training set: X_tr,y_tr
    using validation set: X_val,y_val & class weights: cl_weight
    '''

    def objective(trial):
        s = trial.suggest_int('step',2,5)
        def exponential_decay_fn(epoch):
            return 0.01 * 0.1**(epoch /s )
              
        # building model & searching for the best no. of neural units per layer.
        model = keras.models.Sequential()
        model.add(keras.layers.InputLayer(input_shape=X_tr.shape[1:]))
        for i in range(trial.suggest_int('number',2,5)):
            model.add(keras.layers.Dense(units=trial.suggest_int('units_{}'.format(i),100,500),activation='selu',
                                     kernel_initializer='lecun_normal')) # For self normalization
        model.add(keras.layers.Dense(units=1,activation='sigmoid')) # For binary classification
    
        # Searching for the best learning rate.
        #lr = trial.suggest_float("lr", 1e-5, 1e-1, log=True) 
    
        # Compiling the model
        model.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
        # Defining the Callbacks
        checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
        early_stopping_cb = keras.callbacks.EarlyStopping(patience=10) # 2nd Callback, Stop if validation score doen't improve for
        # 10 epochs  
        lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
        #tensorboard_cb = keras.callbacks.TensorBoard(get_run_logdir()) 
        
        #Fitting the model
        model.fit(X_tr,y_tr,epochs=50,validation_data=(X_val,y_val),batch_size=32,
             class_weight=trial.suggest_categorical('best_weight',cl_weight),
             callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])#,tensorboard_cb])
    
        # Loading the best model 
        model_best = keras.models.load_model('best_model.h5')
    
        # Computing the roc_auc_score for the validation set
        roc_auc_1 = roc_auc_score(y_val,model_best.predict(X_val))
        global best_roc_auc
        # Updating best_roc_auc score
        if roc_auc_1 > best_roc_auc:
            best_roc_auc = roc_auc_1
            model_best.save('Best_model_Selu_Learn.h5')
        
        return roc_auc_1
    
    return objective
    

In [12]:
# Defining the evaluation function for study's best parameters
def train_test_roc_auc(X_tr, y_tr, X_v, y_v, obj_func, cl_weight, n_trials=100):
    ''' Computes the best hyper parameters of the Neural net using the Training set(X_tr,y_tr) & Validation set
    (X_v,y_v), class weights cl_wei & 
    returns Optuna's study's best score & clasifier parameters'''
    
    study = optuna.create_study(direction='maximize')
    study.optimize(obj_func(X_tr, y_tr, X_v, y_v, cl_weight),n_trials)
    best_score = study.best_value
    best_params = study.best_params
    return (best_score,best_params)


In [13]:
# Extracting the best model parameters and best study score
best_study_score,best_study_params = train_test_roc_auc(X_train_red_1, y_train_1, X_val, y_val,objective_wrappper_keras,cl_weight)

[I 2020-10-07 17:29:27,997] A new study created in memory with name: no-name-175d4ad0-ce26-46dd-94b8-71c7a01e1969


  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 29655 samples, validate on 3295 samples
Epoch 1/50
29655/29655 [==============================] - ETA: 24:23 - loss: 1.4258 - accuracy: 0.593 - ETA: 2:04 - loss: 4.5925 - accuracy: 0.619 - ETA: 1:16 - loss: 3.7553 - accuracy: 0.61 - ETA: 58s - loss: 3.2075 - accuracy: 0.6146 - ETA: 41s - loss: 2.6263 - accuracy: 0.645 - ETA: 30s - loss: 2.2893 - accuracy: 0.621 - ETA: 24s - loss: 2.0864 - accuracy: 0.625 - ETA: 21s - loss: 1.9002 - accuracy: 0.652 - ETA: 18s - loss: 1.8077 - accuracy: 0.644 - ETA: 15s - loss: 1.7703 - accuracy: 0.635 - ETA: 13s - loss: 1.6887 - accuracy: 0.645 - ETA: 12s - loss: 1.6595 - accuracy: 0.637 - ETA: 11s - loss: 1.6197 - accuracy: 0.650 - ETA: 11s - loss: 1.5849 - accuracy: 0.650 - ETA: 10s - loss: 1.5733 - accuracy: 0.648 - ETA: 9s - loss: 1.5397 - accuracy: 0.658 - ETA: 9s - loss: 1.5507 - accuracy: 0.65 - ETA: 8s - loss: 1.5334 - accuracy: 0.65 - ETA: 8s - loss: 1.5215 - accuracy: 0.65 - ETA: 7s - 

29655/29655 [==============================] - ETA: 4s - loss: 1.2492 - accuracy: 0.78 - ETA: 3s - loss: 1.0926 - accuracy: 0.79 - ETA: 3s - loss: 1.1148 - accuracy: 0.77 - ETA: 3s - loss: 1.1041 - accuracy: 0.77 - ETA: 3s - loss: 1.1068 - accuracy: 0.75 - ETA: 2s - loss: 1.0847 - accuracy: 0.77 - ETA: 2s - loss: 1.0660 - accuracy: 0.78 - ETA: 2s - loss: 1.0811 - accuracy: 0.77 - ETA: 2s - loss: 1.0732 - accuracy: 0.77 - ETA: 2s - loss: 1.0759 - accuracy: 0.77 - ETA: 2s - loss: 1.0766 - accuracy: 0.77 - ETA: 2s - loss: 1.0730 - accuracy: 0.77 - ETA: 3s - loss: 1.0747 - accuracy: 0.77 - ETA: 2s - loss: 1.0736 - accuracy: 0.77 - ETA: 2s - loss: 1.0620 - accuracy: 0.78 - ETA: 2s - loss: 1.0572 - accuracy: 0.78 - ETA: 2s - loss: 1.0554 - accuracy: 0.78 - ETA: 2s - loss: 1.0478 - accuracy: 0.79 - ETA: 2s - loss: 1.0363 - accuracy: 0.79 - ETA: 2s - loss: 1.0342 - accuracy: 0.79 - ETA: 2s - loss: 1.0307 - accuracy: 0.79 - ETA: 2s - loss: 1.0277 - accuracy: 0.79 - ETA: 2s - loss: 1.0315 - accu

29655/29655 [==============================] - ETA: 4s - loss: 1.2408 - accuracy: 0.75 - ETA: 3s - loss: 0.9311 - accuracy: 0.80 - ETA: 3s - loss: 0.9524 - accuracy: 0.81 - ETA: 3s - loss: 0.9149 - accuracy: 0.82 - ETA: 3s - loss: 0.8991 - accuracy: 0.83 - ETA: 3s - loss: 0.9107 - accuracy: 0.84 - ETA: 3s - loss: 0.9131 - accuracy: 0.84 - ETA: 3s - loss: 0.9440 - accuracy: 0.83 - ETA: 3s - loss: 0.9435 - accuracy: 0.83 - ETA: 2s - loss: 0.9445 - accuracy: 0.83 - ETA: 2s - loss: 0.9443 - accuracy: 0.83 - ETA: 2s - loss: 0.9531 - accuracy: 0.82 - ETA: 2s - loss: 0.9619 - accuracy: 0.82 - ETA: 2s - loss: 0.9768 - accuracy: 0.82 - ETA: 2s - loss: 0.9791 - accuracy: 0.82 - ETA: 2s - loss: 0.9694 - accuracy: 0.82 - ETA: 2s - loss: 0.9581 - accuracy: 0.82 - ETA: 2s - loss: 0.9702 - accuracy: 0.82 - ETA: 2s - loss: 0.9759 - accuracy: 0.82 - ETA: 2s - loss: 0.9804 - accuracy: 0.82 - ETA: 2s - loss: 0.9933 - accuracy: 0.82 - ETA: 2s - loss: 0.9972 - accuracy: 0.82 - ETA: 2s - loss: 0.9955 - accu

29655/29655 [==============================] - ETA: 5s - loss: 0.5569 - accuracy: 0.87 - ETA: 3s - loss: 1.0410 - accuracy: 0.83 - ETA: 3s - loss: 0.9891 - accuracy: 0.82 - ETA: 3s - loss: 1.0793 - accuracy: 0.81 - ETA: 3s - loss: 1.0546 - accuracy: 0.81 - ETA: 3s - loss: 1.0572 - accuracy: 0.80 - ETA: 3s - loss: 1.0543 - accuracy: 0.80 - ETA: 3s - loss: 1.0766 - accuracy: 0.79 - ETA: 3s - loss: 1.0649 - accuracy: 0.80 - ETA: 2s - loss: 1.0684 - accuracy: 0.79 - ETA: 2s - loss: 1.0715 - accuracy: 0.80 - ETA: 2s - loss: 1.0654 - accuracy: 0.80 - ETA: 2s - loss: 1.0677 - accuracy: 0.80 - ETA: 2s - loss: 1.0535 - accuracy: 0.79 - ETA: 2s - loss: 1.0451 - accuracy: 0.80 - ETA: 2s - loss: 1.0361 - accuracy: 0.80 - ETA: 2s - loss: 1.0295 - accuracy: 0.80 - ETA: 2s - loss: 1.0387 - accuracy: 0.80 - ETA: 2s - loss: 1.0356 - accuracy: 0.80 - ETA: 2s - loss: 1.0290 - accuracy: 0.80 - ETA: 2s - loss: 1.0260 - accuracy: 0.80 - ETA: 2s - loss: 1.0223 - accuracy: 0.80 - ETA: 2s - loss: 1.0210 - accu

...

[I 2020-10-07 19:04:18,580] Trial 98 finished with value: 0.8116673611085504 and parameters: {'step': 3, 'number': 2, 'units_0': 279, 'units_1': 140, 'best_weight': {0: 1.0, 1: 11.0}}. Best is trial 20 with value: 0.8160156120368288.


  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 29655 samples, validate on 3295 samples
Epoch 1/50
29655/29655 [==============================] - ETA: 8:55 - loss: 1.9099 - accuracy: 0.34 - ETA: 27s - loss: 3.8855 - accuracy: 0.5967 - ETA: 13s - loss: 2.6515 - accuracy: 0.563 - ETA: 9s - loss: 2.1507 - accuracy: 0.602 - ETA: 7s - loss: 1.9337 - accuracy: 0.62 - ETA: 6s - loss: 1.8303 - accuracy: 0.61 - ETA: 5s - loss: 1.7409 - accuracy: 0.62 - ETA: 4s - loss: 1.6600 - accuracy: 0.62 - ETA: 4s - loss: 1.6260 - accuracy: 0.62 - ETA: 3s - loss: 1.5908 - accuracy: 0.62 - ETA: 3s - loss: 1.5389 - accuracy: 0.63 - ETA: 3s - loss: 1.5048 - accuracy: 0.64 - ETA: 2s - loss: 1.5057 - accuracy: 0.64 - ETA: 2s - loss: 1.4901 - accuracy: 0.64 - ETA: 2s - loss: 1.4844 - accuracy: 0.63 - ETA: 2s - loss: 1.4692 - accuracy: 0.64 - ETA: 2s - loss: 1.4434 - accuracy: 0.64 - ETA: 2s - loss: 1.4284 - accuracy: 0.64 - ETA: 1s - loss: 1.4265 - accuracy: 0.64 - ETA: 1s - loss: 1.4112 - accuracy: 0.

29655/29655 [==============================] - ETA: 3s - loss: 0.7524 - accuracy: 0.78 - ETA: 2s - loss: 1.0677 - accuracy: 0.77 - ETA: 2s - loss: 1.0894 - accuracy: 0.76 - ETA: 2s - loss: 1.0590 - accuracy: 0.76 - ETA: 1s - loss: 1.0784 - accuracy: 0.76 - ETA: 1s - loss: 1.0530 - accuracy: 0.77 - ETA: 1s - loss: 1.0734 - accuracy: 0.77 - ETA: 1s - loss: 1.0650 - accuracy: 0.76 - ETA: 1s - loss: 1.0663 - accuracy: 0.76 - ETA: 1s - loss: 1.0521 - accuracy: 0.77 - ETA: 1s - loss: 1.0495 - accuracy: 0.77 - ETA: 1s - loss: 1.0379 - accuracy: 0.78 - ETA: 1s - loss: 1.0270 - accuracy: 0.78 - ETA: 1s - loss: 1.0389 - accuracy: 0.78 - ETA: 1s - loss: 1.0405 - accuracy: 0.78 - ETA: 1s - loss: 1.0453 - accuracy: 0.77 - ETA: 1s - loss: 1.0449 - accuracy: 0.77 - ETA: 1s - loss: 1.0345 - accuracy: 0.77 - ETA: 1s - loss: 1.0309 - accuracy: 0.78 - ETA: 1s - loss: 1.0291 - accuracy: 0.78 - ETA: 1s - loss: 1.0259 - accuracy: 0.78 - ETA: 0s - loss: 1.0275 - accuracy: 0.78 - ETA: 0s - loss: 1.0323 - accu

29655/29655 [==============================] - ETA: 2s - loss: 0.7167 - accuracy: 0.71 - ETA: 2s - loss: 1.0853 - accuracy: 0.76 - ETA: 2s - loss: 1.0342 - accuracy: 0.77 - ETA: 1s - loss: 0.9774 - accuracy: 0.78 - ETA: 1s - loss: 0.9829 - accuracy: 0.78 - ETA: 1s - loss: 0.9878 - accuracy: 0.78 - ETA: 1s - loss: 0.9817 - accuracy: 0.78 - ETA: 1s - loss: 0.9926 - accuracy: 0.78 - ETA: 1s - loss: 1.0118 - accuracy: 0.78 - ETA: 1s - loss: 1.0126 - accuracy: 0.78 - ETA: 1s - loss: 1.0163 - accuracy: 0.78 - ETA: 1s - loss: 1.0165 - accuracy: 0.78 - ETA: 1s - loss: 1.0230 - accuracy: 0.78 - ETA: 1s - loss: 1.0302 - accuracy: 0.78 - ETA: 1s - loss: 1.0325 - accuracy: 0.78 - ETA: 1s - loss: 1.0252 - accuracy: 0.78 - ETA: 1s - loss: 1.0297 - accuracy: 0.78 - ETA: 1s - loss: 1.0293 - accuracy: 0.78 - ETA: 1s - loss: 1.0332 - accuracy: 0.78 - ETA: 1s - loss: 1.0323 - accuracy: 0.78 - ETA: 1s - loss: 1.0340 - accuracy: 0.78 - ETA: 0s - loss: 1.0295 - accuracy: 0.78 - ETA: 0s - loss: 1.0277 - accu

[I 2020-10-07 19:04:59,929] Trial 99 finished with value: 0.8044213516911811 and parameters: {'step': 5, 'number': 2, 'units_0': 486, 'units_1': 177, 'best_weight': {0: 1.0, 1: 10.0}}. Best is trial 20 with value: 0.8160156120368288.


In [14]:
print('The best roc_auc_score for the study is: ',best_study_score)

The best roc_auc_score for the study is:  0.8160156120368288


In [15]:
print('The best study parameters for the classifier are: ',best_study_params)

The best study parameters for the classifier are:  {'step': 4, 'number': 3, 'units_0': 494, 'units_1': 103, 'units_2': 355, 'best_weight': {0: 1.0, 1: 7.8761}}


In [16]:
# loading the best Neural Network
Best_Model_lr = keras.models.load_model('Best_model_Selu_Learn.h5')

In [17]:
# Printing its summary
Best_Model_lr.summary()

Model: "sequential_20"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_81 (Dense)             (None, 494)               18278     
_________________________________________________________________
dense_82 (Dense)             (None, 103)               50985     
_________________________________________________________________
dense_83 (Dense)             (None, 355)               36920     
_________________________________________________________________
dense_84 (Dense)             (None, 1)                 356       
Total params: 106,539
Trainable params: 106,539
Non-trainable params: 0
_________________________________________________________________


In [8]:
# Defining the function to calculate the roc_auc score for the feature sets
def cal_roc_auc(X, y, cls, f_set, t_set, model_name):
    ''' Calculates the roc auc score using the best study parameters 
        f_set : String: specifies 'full feature', 'Reduced feature'
        t_set: String: specifies 'training', 'test'
        model_name: String: specifies Name of the model '''
        
    y_pred = cls.predict_proba(X)
    print('The roc_auc_score for the {} {} set using the best {} classifier is '.format(f_set,t_set,model_name),roc_auc_score(y,y_pred))

In [19]:
# Calculating the Reduced feature training set roc_auc score using the pretrained Neural Network having 
#best study parameters & weights
cal_roc_auc(X_train_red, y_train, Best_Model_lr, 'Reduced feature', 'training', 'Dense Neural Network')

The roc_auc_score for the Reduced feature training set using the best Dense Neural Network classifier is  0.8134312507518557


In [20]:
# Calculating the Reduced feature test set roc_auc score using the pretrained Neural Network having 
#best study parameters & weights
cal_roc_auc(X_test_red, y_test, Best_Model_lr, 'Reduced feature', 'test', 'Dense Neural Network')

The roc_auc_score for the Reduced feature test set using the best Dense Neural Network classifier is  0.8041722929147601


### Calculating R_R ratio for Best variable layer Dense Neural Network with variable no. of neurons in all the layers

In [22]:
# # Importing train test split from Sklearn to produce validation set
from sklearn.model_selection import train_test_split

In [23]:
# Defining the exponential decay learning rate with step 4.
def exponential_decay_fn(epoch):
            return 0.01 * 0.1**(epoch /4 )

In [24]:
from sklearn.model_selection import StratifiedKFold

In [25]:
# Initializing the K Fold object
cv_strat = StratifiedKFold(10,random_state=42)

In [26]:
# Computing  10 fold  CV predictions on the training set for the Neural Network with variable no. of neurons/layer
scores_variable_neural = []
for train_index, test_index in cv_strat.split(X_train_red, y_train):
    # Creating  Folds
    X_tr, X_tst = X_train_red.loc[train_index], X_train_red.loc[test_index]
    y_tr, y_tst = y_train.loc[train_index], y_train.loc[test_index]
    
    # Splitting the Training set further into training & validation set.
    X_tr_r, X_val, y_tr_r, y_val = train_test_split(X_tr, y_tr, test_size=0.1, random_state=42, stratify=y_tr)
    
    # Loading fresh best variable layer keras model at every iteration for training on 9 folds
    neural = keras.models.load_model('Best_model_Selu_Learn.h5')
    
    # comiling & Training the Neural Net
    neural.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
    # defining Checkpoints
    checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
    early_stopping_cb = keras.callbacks.EarlyStopping(patience=10)# 2nd Callback
    lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
    
    # Fitting The model
    neural.fit(X_tr_r, y_tr_r, epochs=50, validation_data=(X_val,y_val),batch_size=32,
    class_weight={0: 1.0, 1: 7.8761},callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])
    
    # Loading the best Neural model after training & before making predictions
    neural_best = keras.models.load_model('best_model.h5')    
    
    # Saving the predictions for every fold in the scores_variable_neural list
    y_pred = neural_best.predict_proba(X_tst)
    scores_variable_neural.append(roc_auc_score(y_tst,y_pred))
      

  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 26689 samples, validate on 2966 samples
Epoch 1/50
26689/26689 [==============================] - 3s 116us/sample - loss: 1.5665 - accuracy: 0.6659 - val_loss: 2.4770 - val_accuracy: 0.8908
Epoch 2/50
26689/26689 [==============================] - 2s 79us/sample - loss: 1.1286 - accuracy: 0.7238 - val_loss: 1.1467 - val_accuracy: 0.8769
Epoch 3/50
26689/26689 [==============================] - 2s 77us/sample - loss: 1.0266 - accuracy: 0.7660 - val_loss: 1.8375 - val_accuracy: 0.8931
Epoch 4/50
26689/26689 [==============================] - 2s 79us/sample - loss: 0.9855 - accuracy: 0.7950 - val_loss: 0.9604 - val_accuracy: 0.8597
Epoch 5/50
26689/26689 [==============================] - 2s 77us/sample - loss: 0.9705 - accuracy: 0.8109 - val_loss: 0.9473 - val_accuracy: 0.7556
Epoch 6/50
26689/26689 [==============================] - 2s 80us/sample - loss: 0.9580 - accuracy: 0.8135 - val_loss: 0.9468 - val_accuracy: 0.8510
Epoch 

Epoch 11/50
26689/26689 [==============================] - ETA: 0s - loss: 0.9316 - accuracy: 0.82 - 2s 76us/sample - loss: 0.9316 - accuracy: 0.8293 - val_loss: 0.9667 - val_accuracy: 0.8220
Epoch 12/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9318 - accuracy: 0.8284 - val_loss: 0.9693 - val_accuracy: 0.8375
Epoch 13/50
26689/26689 [==============================] - 2s 75us/sample - loss: 0.9311 - accuracy: 0.8283 - val_loss: 0.9717 - val_accuracy: 0.8415
Epoch 14/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9310 - accuracy: 0.8304 - val_loss: 0.9681 - val_accuracy: 0.8345
Epoch 15/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9307 - accuracy: 0.8276 - val_loss: 0.9692 - val_accuracy: 0.8372
  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 26689 samples, validate on 2966 samples
Epoch 1/50
26689/26689 [==============================] - 3s 112us/sample - loss: 1.6051 - accuracy: 0.6618 -

Epoch 18/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9282 - accuracy: 0.8367 - val_loss: 0.9750 - val_accuracy: 0.8422
Epoch 19/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9281 - accuracy: 0.8366 - val_loss: 0.9750 - val_accuracy: 0.8422
Epoch 20/50
26689/26689 [==============================] - 2s 76us/sample - loss: 0.9281 - accuracy: 0.8364 - val_loss: 0.9749 - val_accuracy: 0.8422
Epoch 21/50
26689/26689 [==============================] - 2s 75us/sample - loss: 0.9281 - accuracy: 0.8365 - val_loss: 0.9749 - val_accuracy: 0.8425
Epoch 22/50
26689/26689 [==============================] - 2s 75us/sample - loss: 0.9281 - accuracy: 0.8365 - val_loss: 0.9749 - val_accuracy: 0.8425


In [27]:
print('The reward associated with the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is: ',np.mean(scores_variable_neural))

The reward associated with the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is:  0.7906737465920676


In [28]:
print('The risk associated with the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is: ',np.std( scores_variable_neural))

The risk associated with the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is:  0.01565013769580305


In [29]:
R_R_Ratio_neural = np.mean(scores_variable_neural)/np.std(scores_variable_neural)

In [30]:
print('The reward risk ratio for the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is: ',R_R_Ratio_neural)

The reward risk ratio for the best Dense Neural Network (with variable no.of neurons/layer) Classifier using roc_auc metric is:  50.52183961321345


#### R_R Ratio for the best variable layer Dense Neural Network (with variable no.of neurons/layer) classifier using reduced feature set is: 50.52183961321345

## Observations:
### 1)  The Keras variable layer dense model with variable no. of neurons/layer did  fit the Training set well ,with roc_auc_score comparable to that of other models . But since Neural Networks work best when we have lots of data, we could have seen better results, with the above tuned model, if we had more data. May be tuned neural net with equal no. of neurons/ layer offer better results.
### 2) The R_R ratio for the best Dense Neural Network (with variable no.of neurons/layer) is less than those of tree based bagging models , but more than those of tree based boosting models  ae well as Logistic Regression & SVM Models.

## Model_10:  Keras Variable Layer Dense Model with Equal Neurons , SELU Activation &  Tuned learning rate.

In [36]:
# Re_Initializing train validation split with test size = .1 to provide more Training data to Neural Net 
X_train_red_1, X_val, y_train_1, y_val = train_test_split(X_train_red, y_train, test_size=0.1, random_state=42,
                                                          stratify=y_train)

In [24]:
# defining class weight dictionary list for the imbalanced class
cl_weight = [{0:1.0,1:7.8761},{0:1.0,1:9.0},{0:1.0,1:10.0},{0:1.0,1:11.0},{0:1.0,1:12.0},{0:1.0,1:13.0},{0:1.0,1:14.0}]

In [25]:
# Again defining best roc_auc score
best_roc_auc = 0

In [26]:
# defining the objective function
def objective_wrappper_keras_eq(X_tr, y_tr, X_val, y_val, cl_weight):
    '''
    Optimizes Keras ,neural net with equal no. of neurons in each layer , best parameters 
    on the given training set: X_tr, y_tr using validation set: X_val,y_val & class weights: cl_weight
    
    '''

    def objective(trial):
        s = trial.suggest_int('step',2,5)
        def exponential_decay_fn(epoch):
            return 0.01 * 0.1**(epoch /s )
              
        # building model & searching for the best no. of neural units per layer.
        no_units = trial.suggest_int('no._units',100,500)# No. of Neurons in each layer
        model = keras.models.Sequential()
        model.add(keras.layers.InputLayer(input_shape=X_tr.shape[1:]))
        for i in range(trial.suggest_int('number',2,5)):
            model.add(keras.layers.Dense(units=no_units,activation='selu',
                                     kernel_initializer='lecun_normal')) # For self normalization
        model.add(keras.layers.Dense(units=1,activation='sigmoid'))
    
        # Searching for the best learning rate.
        #lr = trial.suggest_float("lr", 1e-5, 1e-1, log=True) 
    
        # Compiling the model
        model.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
        # Defining the Callbacks
        checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
        early_stopping_cb = keras.callbacks.EarlyStopping(patience=10) # 2nd Callback, Stop if validation score doen't improve for
        # 10 epochs        
        lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
        #tensorboard_cb = keras.callbacks.TensorBoard(get_run_logdir()) 
        
        #Fitting the model
        model.fit(X_tr,y_tr,epochs=50,validation_data=(X_val,y_val),batch_size=32,
             class_weight=trial.suggest_categorical('best_weight',cl_weight),
             callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])#,tensorboard_cb])
    
        # Loading the best model 
        model_best = keras.models.load_model('best_model.h5')
    
        # Computing the roc_auc_score for the validation set
        roc_auc_1 = roc_auc_score(y_val,model_best.predict(X_val))
        global best_roc_auc
        # Updating best_roc_auc score
        if roc_auc_1 > best_roc_auc:
            best_roc_auc = roc_auc_1
            model_best.save('Best_model_Selu_eq_Learn.h5')
        
        return roc_auc_1
    
    return objective

In [27]:
# Extracting the best model parameters and best study score
best_study_score,best_study_params = train_test_roc_auc(X_train_red_1, y_train_1, X_val, y_val, objective_wrappper_keras_eq, cl_weight)

[I 2020-10-07 19:40:07,046] A new study created in memory with name: no-name-aa7f216d-df91-4935-ad46-878073716ed3


  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 29655 samples, validate on 3295 samples
Epoch 1/50
29655/29655 [==============================] - ETA: 12:37 - loss: 1.8607 - accuracy: 0.281 - ETA: 52s - loss: 90.8754 - accuracy: 0.512 - ETA: 26s - loss: 45.8780 - accuracy: 0.43 - ETA: 19s - loss: 32.1153 - accuracy: 0.49 - ETA: 14s - loss: 24.0880 - accuracy: 0.50 - ETA: 11s - loss: 19.3916 - accuracy: 0.51 - ETA: 10s - loss: 16.2944 - accuracy: 0.52 - ETA: 8s - loss: 14.2465 - accuracy: 0.5191 - ETA: 7s - loss: 12.6735 - accuracy: 0.508 - ETA: 7s - loss: 11.3252 - accuracy: 0.498 - ETA: 6s - loss: 10.3262 - accuracy: 0.501 - ETA: 6s - loss: 9.5125 - accuracy: 0.502 - ETA: 5s - loss: 8.8351 - accuracy: 0.50 - ETA: 5s - loss: 8.2877 - accuracy: 0.50 - ETA: 4s - loss: 7.7806 - accuracy: 0.50 - ETA: 4s - loss: 7.3425 - accuracy: 0.51 - ETA: 4s - loss: 6.9978 - accuracy: 0.52 - ETA: 4s - loss: 6.6468 - accuracy: 0.52 - ETA: 3s - loss: 6.3448 - accuracy: 0.53 - ETA: 3s - loss: 6.

29655/29655 [==============================] - ETA: 4s - loss: 1.4034 - accuracy: 0.09 - ETA: 3s - loss: 1.4132 - accuracy: 0.09 - ETA: 3s - loss: 1.4062 - accuracy: 0.09 - ETA: 2s - loss: 1.4672 - accuracy: 0.10 - ETA: 2s - loss: 1.4876 - accuracy: 0.10 - ETA: 2s - loss: 1.4914 - accuracy: 0.10 - ETA: 2s - loss: 1.5067 - accuracy: 0.11 - ETA: 2s - loss: 1.5133 - accuracy: 0.11 - ETA: 2s - loss: 1.5175 - accuracy: 0.11 - ETA: 2s - loss: 1.5255 - accuracy: 0.11 - ETA: 2s - loss: 1.5280 - accuracy: 0.11 - ETA: 2s - loss: 1.5201 - accuracy: 0.11 - ETA: 2s - loss: 1.5140 - accuracy: 0.11 - ETA: 2s - loss: 1.5143 - accuracy: 0.11 - ETA: 2s - loss: 1.5135 - accuracy: 0.11 - ETA: 2s - loss: 1.5117 - accuracy: 0.11 - ETA: 2s - loss: 1.5062 - accuracy: 0.11 - ETA: 2s - loss: 1.5016 - accuracy: 0.11 - ETA: 2s - loss: 1.5041 - accuracy: 0.11 - ETA: 2s - loss: 1.5014 - accuracy: 0.11 - ETA: 1s - loss: 1.5041 - accuracy: 0.11 - ETA: 1s - loss: 1.5025 - accuracy: 0.11 - ETA: 1s - loss: 1.5044 - accu

29655/29655 [==============================] - ETA: 3s - loss: 1.4042 - accuracy: 0.09 - ETA: 2s - loss: 1.5591 - accuracy: 0.12 - ETA: 2s - loss: 1.5885 - accuracy: 0.12 - ETA: 2s - loss: 1.5652 - accuracy: 0.12 - ETA: 2s - loss: 1.5484 - accuracy: 0.12 - ETA: 2s - loss: 1.5342 - accuracy: 0.11 - ETA: 2s - loss: 1.5381 - accuracy: 0.11 - ETA: 2s - loss: 1.5466 - accuracy: 0.12 - ETA: 2s - loss: 1.5241 - accuracy: 0.11 - ETA: 2s - loss: 1.5154 - accuracy: 0.11 - ETA: 2s - loss: 1.5044 - accuracy: 0.11 - ETA: 2s - loss: 1.4921 - accuracy: 0.11 - ETA: 2s - loss: 1.4908 - accuracy: 0.11 - ETA: 2s - loss: 1.4885 - accuracy: 0.10 - ETA: 2s - loss: 1.4942 - accuracy: 0.11 - ETA: 2s - loss: 1.4998 - accuracy: 0.11 - ETA: 2s - loss: 1.4926 - accuracy: 0.11 - ETA: 2s - loss: 1.4905 - accuracy: 0.11 - ETA: 2s - loss: 1.4931 - accuracy: 0.11 - ETA: 1s - loss: 1.4933 - accuracy: 0.11 - ETA: 1s - loss: 1.4940 - accuracy: 0.11 - ETA: 1s - loss: 1.4948 - accuracy: 0.11 - ETA: 1s - loss: 1.4967 - accu

29655/29655 [==============================] - ETA: 3s - loss: 1.4063 - accuracy: 0.09 - ETA: 2s - loss: 1.4820 - accuracy: 0.10 - ETA: 3s - loss: 1.4917 - accuracy: 0.11 - ETA: 3s - loss: 1.4832 - accuracy: 0.10 - ETA: 3s - loss: 1.4894 - accuracy: 0.10 - ETA: 3s - loss: 1.4856 - accuracy: 0.10 - ETA: 3s - loss: 1.4839 - accuracy: 0.10 - ETA: 3s - loss: 1.4986 - accuracy: 0.11 - ETA: 2s - loss: 1.5006 - accuracy: 0.11 - ETA: 2s - loss: 1.5184 - accuracy: 0.11 - ETA: 2s - loss: 1.5196 - accuracy: 0.11 - ETA: 2s - loss: 1.5151 - accuracy: 0.11 - ETA: 2s - loss: 1.5135 - accuracy: 0.11 - ETA: 2s - loss: 1.5062 - accuracy: 0.11 - ETA: 2s - loss: 1.5056 - accuracy: 0.11 - ETA: 2s - loss: 1.5051 - accuracy: 0.11 - ETA: 2s - loss: 1.4999 - accuracy: 0.11 - ETA: 2s - loss: 1.4955 - accuracy: 0.11 - ETA: 2s - loss: 1.5059 - accuracy: 0.11 - ETA: 2s - loss: 1.5056 - accuracy: 0.11 - ETA: 2s - loss: 1.5062 - accuracy: 0.11 - ETA: 2s - loss: 1.5006 - accuracy: 0.11 - ETA: 2s - loss: 1.5112 - accu

...

29655/29655 [==============================] - ETA: 2s - loss: 1.0800 - accuracy: 0.75 - ETA: 2s - loss: 0.8783 - accuracy: 0.82 - ETA: 1s - loss: 0.8638 - accuracy: 0.83 - ETA: 1s - loss: 0.9044 - accuracy: 0.82 - ETA: 1s - loss: 0.9249 - accuracy: 0.82 - ETA: 1s - loss: 0.9475 - accuracy: 0.81 - ETA: 1s - loss: 0.9622 - accuracy: 0.81 - ETA: 1s - loss: 0.9484 - accuracy: 0.81 - ETA: 1s - loss: 0.9418 - accuracy: 0.82 - ETA: 1s - loss: 0.9385 - accuracy: 0.82 - ETA: 1s - loss: 0.9423 - accuracy: 0.81 - ETA: 1s - loss: 0.9446 - accuracy: 0.81 - ETA: 1s - loss: 0.9391 - accuracy: 0.82 - ETA: 1s - loss: 0.9406 - accuracy: 0.82 - ETA: 1s - loss: 0.9345 - accuracy: 0.82 - ETA: 1s - loss: 0.9417 - accuracy: 0.82 - ETA: 1s - loss: 0.9272 - accuracy: 0.82 - ETA: 1s - loss: 0.9292 - accuracy: 0.82 - ETA: 1s - loss: 0.9289 - accuracy: 0.82 - ETA: 1s - loss: 0.9349 - accuracy: 0.82 - ETA: 0s - loss: 0.9336 - accuracy: 0.82 - ETA: 0s - loss: 0.9322 - accuracy: 0.82 - ETA: 0s - loss: 0.9384 - accu

29655/29655 [==============================] - ETA: 3s - loss: 0.7318 - accuracy: 0.90 - ETA: 1s - loss: 0.9337 - accuracy: 0.82 - ETA: 1s - loss: 0.9337 - accuracy: 0.81 - ETA: 1s - loss: 0.9788 - accuracy: 0.81 - ETA: 1s - loss: 0.9714 - accuracy: 0.81 - ETA: 1s - loss: 0.9640 - accuracy: 0.81 - ETA: 1s - loss: 0.9441 - accuracy: 0.82 - ETA: 1s - loss: 0.9388 - accuracy: 0.82 - ETA: 1s - loss: 0.9311 - accuracy: 0.82 - ETA: 1s - loss: 0.9401 - accuracy: 0.82 - ETA: 1s - loss: 0.9389 - accuracy: 0.82 - ETA: 1s - loss: 0.9432 - accuracy: 0.82 - ETA: 1s - loss: 0.9472 - accuracy: 0.82 - ETA: 1s - loss: 0.9399 - accuracy: 0.82 - ETA: 1s - loss: 0.9406 - accuracy: 0.82 - ETA: 1s - loss: 0.9338 - accuracy: 0.82 - ETA: 1s - loss: 0.9455 - accuracy: 0.82 - ETA: 1s - loss: 0.9451 - accuracy: 0.82 - ETA: 1s - loss: 0.9519 - accuracy: 0.82 - ETA: 1s - loss: 0.9587 - accuracy: 0.82 - ETA: 0s - loss: 0.9539 - accuracy: 0.82 - ETA: 0s - loss: 0.9464 - accuracy: 0.82 - ETA: 0s - loss: 0.9465 - accu

29655/29655 [==============================] - ETA: 2s - loss: 0.6216 - accuracy: 0.84 - ETA: 2s - loss: 0.9055 - accuracy: 0.79 - ETA: 1s - loss: 0.9593 - accuracy: 0.80 - ETA: 1s - loss: 0.9438 - accuracy: 0.81 - ETA: 1s - loss: 0.9498 - accuracy: 0.82 - ETA: 1s - loss: 0.9187 - accuracy: 0.82 - ETA: 1s - loss: 0.9173 - accuracy: 0.82 - ETA: 1s - loss: 0.9207 - accuracy: 0.82 - ETA: 1s - loss: 0.9236 - accuracy: 0.82 - ETA: 1s - loss: 0.9314 - accuracy: 0.82 - ETA: 1s - loss: 0.9348 - accuracy: 0.82 - ETA: 1s - loss: 0.9370 - accuracy: 0.82 - ETA: 1s - loss: 0.9383 - accuracy: 0.82 - ETA: 1s - loss: 0.9366 - accuracy: 0.82 - ETA: 1s - loss: 0.9331 - accuracy: 0.82 - ETA: 1s - loss: 0.9291 - accuracy: 0.82 - ETA: 1s - loss: 0.9257 - accuracy: 0.82 - ETA: 1s - loss: 0.9246 - accuracy: 0.82 - ETA: 1s - loss: 0.9274 - accuracy: 0.82 - ETA: 1s - loss: 0.9309 - accuracy: 0.82 - ETA: 0s - loss: 0.9336 - accuracy: 0.82 - ETA: 0s - loss: 0.9309 - accuracy: 0.82 - ETA: 0s - loss: 0.9304 - accu

29655/29655 [==============================] - ETA: 2s - loss: 1.3123 - accuracy: 0.81 - ETA: 1s - loss: 0.7905 - accuracy: 0.82 - ETA: 1s - loss: 0.8516 - accuracy: 0.82 - ETA: 1s - loss: 0.8802 - accuracy: 0.82 - ETA: 1s - loss: 0.8962 - accuracy: 0.82 - ETA: 1s - loss: 0.8960 - accuracy: 0.82 - ETA: 1s - loss: 0.9236 - accuracy: 0.82 - ETA: 1s - loss: 0.9348 - accuracy: 0.82 - ETA: 1s - loss: 0.9355 - accuracy: 0.82 - ETA: 1s - loss: 0.9273 - accuracy: 0.82 - ETA: 1s - loss: 0.9414 - accuracy: 0.82 - ETA: 1s - loss: 0.9462 - accuracy: 0.82 - ETA: 1s - loss: 0.9449 - accuracy: 0.82 - ETA: 1s - loss: 0.9417 - accuracy: 0.82 - ETA: 1s - loss: 0.9406 - accuracy: 0.82 - ETA: 1s - loss: 0.9374 - accuracy: 0.82 - ETA: 1s - loss: 0.9286 - accuracy: 0.82 - ETA: 1s - loss: 0.9242 - accuracy: 0.82 - ETA: 1s - loss: 0.9288 - accuracy: 0.82 - ETA: 1s - loss: 0.9293 - accuracy: 0.82 - ETA: 0s - loss: 0.9314 - accuracy: 0.82 - ETA: 0s - loss: 0.9344 - accuracy: 0.82 - ETA: 0s - loss: 0.9384 - accu

[I 2020-10-07 21:12:07,331] Trial 99 finished with value: 0.8106349165379184 and parameters: {'step': 4, 'no._units': 176, 'number': 2, 'best_weight': {0: 1.0, 1: 7.8761}}. Best is trial 41 with value: 0.8160736870439269.


In [28]:
print('The best roc_auc_score for the study is: ',best_study_score)

The best roc_auc_score for the study is:  0.8160736870439269


In [29]:
print('The best study parameters for the classifier are: ',best_study_params)

The best study parameters for the classifier are:  {'step': 4, 'no._units': 125, 'number': 2, 'best_weight': {0: 1.0, 1: 10.0}}


In [30]:
# loading the best Neural Network
Best_Model_eq = keras.models.load_model('Best_model_Selu_eq_Learn.h5')

In [31]:
# Printing its summary
Best_Model_eq.summary()

Model: "sequential_145"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_545 (Dense)            (None, 125)               4625      
_________________________________________________________________
dense_546 (Dense)            (None, 125)               15750     
_________________________________________________________________
dense_547 (Dense)            (None, 1)                 126       
Total params: 20,501
Trainable params: 20,501
Non-trainable params: 0
_________________________________________________________________


In [32]:
# Calculating the Reduced feature training set roc_auc score using the Dense Neural Network with equal no. of Neurons/layer
# having best study parameters & weights
cal_roc_auc(X_train_red, y_train, Best_Model_eq, 'Reduced feature', 'training', 'Dense Neural Network with equal no. of Nodes')

The roc_auc_score for the Reduced feature training set using the best Dense Neural Network with equal no. of Nodes classifier is  0.8057215965111534


In [33]:
# Calculating the Reduced feature test set roc_auc score using the Dense Neural Network with equal no. of Neurons/layer
# having best study parameters & weights
cal_roc_auc(X_test_red, y_test, Best_Model_eq, 'Reduced feature', 'test', 'Dense Neural Network with equal no. of Nodes')

The roc_auc_score for the Reduced feature test set using the best Dense Neural Network with equal no. of Nodes classifier is  0.805243687791877


### Calculating R_R ratio for Best Dense Neural Network with equal no. of neurons in all the layers.

In [31]:
# Computing  10 fold  CV predictions on the training set for the Neural Network with equal no. of neurons in eaxh layer
scores_equal_neural = []
for train_index, test_index in cv_strat.split(X_train_red, y_train):
    # Creating  Folds
    X_tr, X_tst = X_train_red.loc[train_index], X_train_red.loc[test_index]
    y_tr, y_tst = y_train.loc[train_index], y_train.loc[test_index]
    
    # Splitting the Training set further into training & validation set.
    X_tr_r, X_val, y_tr_r, y_val = train_test_split(X_tr, y_tr, test_size=0.1, random_state=42, stratify=y_tr)
    
    # Loading fresh best variable layer keras model at every iteration for training on 9 folds
    neural = keras.models.load_model('Best_model_Selu_eq_Learn.h5')
    
    # comiling & Training the Neural Net
    neural.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
    # defining Checkpoints
    checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
    early_stopping_cb = keras.callbacks.EarlyStopping(patience=10)# 2nd Callback
    lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
    
    # Fitting The model
    neural.fit(X_tr_r, y_tr_r, epochs=50, validation_data=(X_val,y_val),batch_size=32,
    class_weight={0: 1.0, 1: 10},callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])
    
    # Loading the best Neural model after training & before making predictions
    neural_best = keras.models.load_model('best_model.h5')    
    
    # Saving the predictions for every fold in the scores list
    y_pred = neural_best.predict_proba(X_tst)
    scores_equal_neural.append(roc_auc_score(y_tst,y_pred))
      

  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 26689 samples, validate on 2966 samples
Epoch 1/50
26689/26689 [==============================] - 3s 99us/sample - loss: 1.2069 - accuracy: 0.6940 - val_loss: 1.8202 - val_accuracy: 0.7532
Epoch 2/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.1462 - accuracy: 0.7274 - val_loss: 1.5435 - val_accuracy: 0.8287
Epoch 3/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.1055 - accuracy: 0.7551 - val_loss: 1.1213 - val_accuracy: 0.8260
Epoch 4/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0888 - accuracy: 0.7706 - val_loss: 1.0560 - val_accuracy: 0.8365
Epoch 5/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0744 - accuracy: 0.7844 - val_loss: 1.0592 - val_accuracy: 0.7384
Epoch 6/50
26689/26689 [==============================] - 2s 80us/sample - loss: 1.0649 - accuracy: 0.7775 - val_loss: 1.0722 - val_accuracy: 0.6935
Epoch 7

26689/26689 [==============================] - 2s 72us/sample - loss: 1.0477 - accuracy: 0.7865 - val_loss: 1.0876 - val_accuracy: 0.8004
Epoch 9/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0445 - accuracy: 0.7883 - val_loss: 1.0847 - val_accuracy: 0.7825
Epoch 10/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0423 - accuracy: 0.7833 - val_loss: 1.0865 - val_accuracy: 0.7994
Epoch 11/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0413 - accuracy: 0.7889 - val_loss: 1.0864 - val_accuracy: 0.7987
Epoch 12/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0406 - accuracy: 0.7882 - val_loss: 1.0857 - val_accuracy: 0.7947
Epoch 13/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0402 - accuracy: 0.7861 - val_loss: 1.0858 - val_accuracy: 0.7960
Epoch 14/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0400 - accuracy: 0.7855 - val

Epoch 25/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 26/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 27/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 28/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 29/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 30/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy: 0.7965 - val_loss: 1.0700 - val_accuracy: 0.8098
Epoch 31/50
26689/26689 [==============================] - 2s 73us/sample - loss: 1.0401 - accuracy:

Epoch 16/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0390 - accuracy: 0.7985 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 17/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0390 - accuracy: 0.7981 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 18/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0389 - accuracy: 0.7982 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 19/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0389 - accuracy: 0.7982 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 20/50
26689/26689 [==============================] - 2s 71us/sample - loss: 1.0389 - accuracy: 0.7981 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 21/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0389 - accuracy: 0.7981 - val_loss: 1.0865 - val_accuracy: 0.8058
Epoch 22/50
26689/26689 [==============================] - 2s 72us/sample - loss: 1.0389 - accuracy:

In [32]:
print('The reward associated with the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is: ',np.mean(scores_equal_neural))

The reward associated with the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is:  0.7940878170779518


In [33]:
print('The risk associated with the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is: ',np.std( scores_equal_neural))

The risk associated with the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is:  0.015282742409472862


In [34]:
R_R_Ratio_neural_eq = np.mean(scores_equal_neural)/np.std(scores_equal_neural)

In [35]:
print('The reward risk ratio for the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is: ',R_R_Ratio_neural_eq)

The reward risk ratio for the best Dense Neural Network (with equal no.of neurons/layer) Classifier using roc_auc metric is:  51.95977238913247


#### R_R Ratio for the best Dense Neural Network (with equal no.of neurons/layer) classifier using reduced feature set is: 51.95977238913247

## Observations:
### 1)  The Keras dense model with equal no. of neurons fitted the Training set very well, with test set roc_auc_score only less than those of tree based bagging & boosting models &  beating the one associated with the  previous more flexible  neural network, while employing fewer layers & substantially less no. of tunable parameters.
### 2) The R_R ratio of the dense model with equal no. of neurons/layer,  is beaten only by those of Tree based bagging models & is quite high  as compared to other classes of models. Hence after considering all the aspects, this model is the 2nd choice after RF Classifier till now.